In [1]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:85% !important; }</style>"))

In [2]:
import os
from utils import boxplots_utils
import pandas as pd
from termcolor import colored
import numpy as np
from collections import OrderedDict
import matplotlib.pyplot as plt
from natsort import natsorted
import sys
from utils import boxplots_utils



# Display pandas df without truncation
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)
pd.set_option('display.max_colwidth', None)

# Numpy array printed with higher width
# np.set_printoptions(edgeitems=30, linewidth=100000, formatter=dict(float=lambda x: "%.3g" % x))

In [ ]:
num_robots = 24
num_areas = 8

In [5]:
results_folder = '/home/luigi/Documents/ARGoS/argos_results_scripts/DHTF/results_adaptive/random_mixed/random_mixed_2021-05-05_robots#24_timeout#6_redAreas#4_1800seconds'

In [6]:
if not os.path.isdir(results_folder):
    print(colored("Error, " + results_folder + " does not exist", 'red'))
else:
    print(colored("OK, " + results_folder + " exists", 'green'))

OK, /home/luigi/Documents/ARGoS/argos_results_scripts/DHTF/results_adaptive/random_mixed/random_mixed_2021-05-05_robots#24_timeout#6_redAreas#4_1800seconds exists


In [25]:
# df_area_client = pd.DataFrame()
# df_area_server = pd.DataFrame()
# df_task_client = pd.DataFrame()
# df_task_server = pd.DataFrame()
# df_kilo_client = pd.DataFrame()
# df_kilo_server = pd.DataFrame()

evaluate = False
for filename in natsorted(os.listdir(results_folder)):
#     print('\t filename: ', filename)
    seed = filename.split("_")[0]
    if seed == 'seed#2':
        break
    
    if filename.endswith("areaLOG_client.tsv"):
        if not os.path.getsize(os.path.join(results_folder, filename)) > 0:
            print(colored("\tWARNING, empty file at:" + filename, 'red'))
            continue
        print('\tfilename: ', filename)
        df_area_client = pd.read_csv(os.path.join(results_folder, filename), sep="\t",
                                     header=None)

    if filename.endswith("areaLOG_server.tsv"):
        if not os.path.getsize(os.path.join(results_folder, filename)) > 0:
            print(colored("\tWARNING, empty file at:" + filename, 'red'))
            continue
        print('\tfilename: ', filename)
        df_area_server = pd.read_csv(os.path.join(results_folder, filename), sep="\t",
                                     header=None)

    if filename.endswith("kiloLOG_client.tsv"):
        if not os.path.getsize(os.path.join(results_folder, filename)) > 0:
            print(colored("\tWARNING, empty file at:" + filename, 'red'))
            continue
        print('\tfilename: ', filename)
        df_kilo_client = pd.read_csv(os.path.join(results_folder, filename), sep="\t",
                                     header=None)

    if filename.endswith("kiloLOG_server.tsv"):
        if not os.path.getsize(os.path.join(results_folder, filename)) > 0:
            print(colored("\tWARNING, empty file at:" + filename, 'red'))
            continue
        print('\tfilename: ', filename, end='\n')
        df_kilo_server = pd.read_csv(os.path.join(results_folder, filename), sep="\t",
                                     header=None)
        evaluate = True
        
        
        
        
    if evaluate:
        
        '''Kilo log'''
        if len(df_kilo_client.columns) > 145:
            print("Cutting null elements in client kilo df")
            df_kilo_client.drop(df_kilo_client.columns[len(df_kilo_client.columns) - 1], axis=1, inplace=True)

        if len(df_kilo_server.columns) > 145:
            print("Cutting null elements in server kilo df")
            df_kilo_server.drop(df_kilo_server.columns[len(df_kilo_server.columns) - 1], axis=1, inplace=True)

        col_kilo_labels = ['time']
        for i in range(0, len(df_kilo_server.columns) - 1, 6):
            #     print(i,end=", ")
            col_kilo_labels += ['id' + str(i // 6), 'state' + str(i // 6), 'posx' + str(i // 6), 'posy' + str(i // 6),
                                'ori' + str(i // 6), 'same_state' + str(i // 6)]

        col_kilo_to_drop = []
        for i in range((len(df_kilo_server.columns) - 1) // 6):
            #     print(i,end=", ")
            col_kilo_to_drop += ['same_state' + str(i)]

        df_kilo_server.columns = col_kilo_labels
        df_kilo_client.columns = col_kilo_labels
        df_kilo_server = df_kilo_server.drop(col_kilo_to_drop, axis=1)
        df_kilo_client = df_kilo_client.drop(col_kilo_to_drop, axis=1)

        # kID0_client = df_kilo_client.iloc[:, :6]
        # kID0_server = df_kilo_server.iloc[:, :6]
        
        '''Area log'''
        col_area_labels = ['time']
        for i in range(0, len(df_area_server.columns) - 2, 6):
            # print(i, end=", ")
            col_area_labels += ['id' + str(i // 6), 'posx' + str(i // 6), 'posy' + str(i // 6), 'color' + str(i // 6),
                                'completed' + str(i // 6), 'contained' + str(i // 6)]

        # Remove last empty col and assign labels to df_area_server
        if len(df_area_server.columns) > 49:
            print("Cutting null elements in area server df")
            df_area_server.drop(df_area_server.columns[len(df_area_server.columns) - 1], axis=1, inplace=True)
        df_area_server.columns = col_area_labels

        # First df_area_client row contains garbage, so is substituted with the second row except for the time,
        # then remove Nan values in [:,49:]
        if len(df_area_client.columns) > 49:
            print("Cutting null elements in area client df")
            df_area_client.loc[0, 1:] = df_area_client.loc[1, 1:]
            df_area_client = df_area_client.drop(np.arange(49, len(df_area_client.columns)), axis=1)
        df_area_client.columns = col_area_labels
        
        
        '''Get area positions and colors'''
        area_pos_label = []
        for i in range(num_areas):
            area_pos_label += ["posx"+str(i)]
            area_pos_label += ["posy"+str(i)]
        # area_pos_label

        areas_pos = df_area_client[area_pos_label].iloc[0, :].values
        areas_pos = areas_pos.reshape(-1,2)
        print(areas_pos)
        
        df_kilo_client_temp = df_kilo_client.copy()#.iloc[:20,:26]
        df_kilo_server_temp = df_kilo_server.copy()
        df_kilo_server_temp.iloc[:10,:]
        
        '''Area color df'''
        color_list = ["color" + str(i) for i in range(num_areas)]
        df_area3_s = df_area_server.iloc[:1, :][color_list]
        df_area3_c = df_area_client.iloc[:1, :][color_list]
        for i,idx in enumerate(range(1,len(df_area3_c.columns)*2,2)):
        #     print(i, ' ', idx)
            df_area3_c.insert(loc=idx, column='other_col'+str(i), value=df_area3_s.iloc[0][i])

        client = [col for col in df_area3_c.columns if 'color' in col]
        server = [col for col in df_area3_c.columns if 'other_col' in col]
        df_area_colors = pd.lreshape(df_area3_c, {'color_client' : client, 'color_server' : server})
        
        area_type = []
        for area in df_area_colors.values:
            if(area[0] == 0 and area[1] == 0):
                area_type += ['BB']
            if(area[0] == 0 and area[1] == 1):
                area_type += ['BR']
            if(area[0] == 1 and area[1] == 0):
                area_type += ['RB']
            if(area[0] == 1 and area[1] == 1):
                area_type += ['RR']
        
        df_area_colors.insert(loc=2, column='area_type', value=area_type)
        
        '''For the server'''
        for i,kilo_id in enumerate(np.arange(1, len(df_kilo_server_temp.columns), 5)):
            print(colored("kilo_id:"+str((kilo_id-1)//5), 'blue'))
        #     print(df_kilo_client_temp.iloc[:20, kilo_id+2:kilo_id+4].values, end='\n\n')
            kilo_pos = df_kilo_server_temp.iloc[:, kilo_id+i+2:kilo_id+i+4].values
        #     print(kilo_pos)
            in_area=np.empty(kilo_pos.shape[0], dtype=int); in_area.fill(-1)
            for area_idx, area_pos in enumerate(areas_pos):
            #     print(area_idx,' ', area_pos)
                dist = np.linalg.norm(kilo_pos-area_pos, axis=1)
            #     print(dist, end='\n\n')
                in_area = np.where(dist < 0.1, df_area_colors.iloc[area_idx][-1][::-1], in_area)
        #     in_area = np.where(in_area == -1, np.NaN, in_area)
        #     print(in_area)
            df_kilo_server_temp.insert(loc=int(kilo_id+i+2), column='area_type'+str(i), value=in_area)

            
        '''For the client'''
        for i,kilo_id in enumerate(np.arange(1, len(df_kilo_client_temp.columns), 5)):
            print(colored("kilo_id:"+str((kilo_id-1)//5), 'blue'))
        #     print(df_kilo_client_temp.iloc[:20, kilo_id+2:kilo_id+4].values, end='\n\n')
            kilo_pos = df_kilo_client_temp.iloc[:, kilo_id+i+2:kilo_id+i+4].values
        #     print(kilo_pos)
            in_area=np.empty(kilo_pos.shape[0], dtype=int); in_area.fill(-1)
            for area_idx, area_pos in enumerate(areas_pos):
            #     print(area_idx,' ', area_pos)
                dist = np.linalg.norm(kilo_pos-area_pos, axis=1)
            #     print(dist, end='\n\n')
                in_area = np.where(dist < 0.1, df_area_colors.iloc[area_idx][-1], in_area)
        #     in_area = np.where(in_area == -1, np.NaN, in_area)
        #     print(in_area)
            df_kilo_client_temp.insert(loc=int(kilo_id+i+2), column='area_type'+str(i), value=in_area)
            
        '''Save pickle file'''
#         kilo_resume = [["state" + str(i), "area_type" + str(i)] for i in range(num_robots)]
#         kilo_resume = np.reshape(kilo_resume, (-1))
        server_kilo_resume = df_kilo_server_temp.iloc[:][kilo_resume]
        client_kilo_resume = df_kilo_client_temp.iloc[:][kilo_resume]
        total_exp_df = df_kilo_client_temp.join(df_kilo_server_temp, lsuffix='_c', rsuffix='_s')

	filename:  seed#1_areaLOG_client.tsv
	filename:  seed#1_areaLOG_server.tsv
	filename:  seed#1_kiloLOG_client.tsv
	filename:  seed#1_kiloLOG_server.tsv
Cutting null elements in client kilo df
Cutting null elements in server kilo df
Cutting null elements in area server df
Cutting null elements in area client df
[[-0.125  0.375]
 [ 0.125  0.375]
 [ 0.125  0.125]
 [ 0.375  0.125]
 [-0.375 -0.125]
 [ 0.125 -0.125]
 [-0.125 -0.375]
 [ 0.125 -0.375]]
kilo_id:0
kilo_id:1
kilo_id:2
kilo_id:3
kilo_id:4
kilo_id:5
kilo_id:6
kilo_id:7
kilo_id:8
kilo_id:9
kilo_id:10
kilo_id:11
kilo_id:12
kilo_id:13
kilo_id:14
kilo_id:15
kilo_id:16
kilo_id:17
kilo_id:18
kilo_id:19
kilo_id:20
kilo_id:21
kilo_id:22
kilo_id:23
kilo_id:0
kilo_id:1
kilo_id:2
kilo_id:3
kilo_id:4
kilo_id:5
kilo_id:6
kilo_id:7
kilo_id:8
kilo_id:9
kilo_id:10
kilo_id:11
kilo_id:12
kilo_id:13
kilo_id:14
kilo_id:15
kilo_id:16
kilo_id:17
kilo_id:18
kilo_id:19
kilo_id:20
kilo_id:21
kilo_id:22
kilo_id:23


In [23]:
df_kilo_server_temp

time  id0  state0 area_type0   posx0   posy0    ori0  id1  state1  \
0       0.1    0       0         BR -0.2084  0.3611 -2.0288    1       0   
1       2.0    0       0         -1 -0.2237  0.3531 -2.9712    1       0   
2       4.0    0       0         -1 -0.2434  0.3497 -2.9712    1       0   
3       6.0    0       0         -1 -0.2632  0.3464 -2.9712    1       0   
4       8.0    0       0         -1 -0.2829  0.3430 -2.9712    1       0   
5      10.0    0       0         -1 -0.3026  0.3396 -2.9712    1       0   
6      12.0    0       0         -1 -0.3223  0.3362 -2.9712    1       0   
7      14.0    0       0         -1 -0.3381  0.3259 -2.1858    1       0   
8      16.0    0       0         -1 -0.3496  0.3096 -2.1858    1       0   
9      18.0    0       0         -1 -0.3502  0.2910 -1.2434    1       0   
10     20.0    0       0         -1 -0.3437  0.2721 -1.2434    1       0   
11     22.0    0       0         -1 -0.3373  0.2532 -1.2434    1       0   
12     24.0    0       0         -1 -0.3309  0.2342 -1.2434    1       0   
13     26.0    0       0         -1 -0.3244  0.2153 -1.2434    1       0   
14     28.0    0       0         -1 -0.3180  0.1963 -1.2434    1       0   
15     30.0    0       0         -1 -0.3116  0.1774 -1.2434    1       0   
16     32.0    0       0         -1 -0.3051  0.1585 -1.2434    1       0   
17     34.0    0       0         -1 -0.2923  0.1456  0.0054    1       0   
18     36.0    0       0         -1 -0.2729  0.1497  0.0211    1       0   
19     38.0    0       0         -1 -0.2596  0.1381 -1.5497    1       0   
20     40.0    0       0         -1 -0.2608  0.1182 -1.6361    1       0   
21     42.0    0       0         -1 -0.2621  0.0982 -1.6361    1       0   
22     44.0    0       0         -1 -0.2634  0.0783 -1.6361    1       0   
23     46.0    0       0         -1 -0.2647  0.0583 -1.6361    1       0   
24     48.0    0       0         -1 -0.2661  0.0384 -1.7853    1       0   
25     50.0    0       0         -1 -0.2805  0.0282  2.9271    1       0   
26     52.0    0       0         -1 -0.2986  0.0365  2.6836    1       0   
27     54.0    0       0         -1 -0.3165  0.0453  2.6836    1       0   
28     56.0    0       0         -1 -0.3344  0.0542  2.6836    1       0   
29     58.0    0       0         -1 -0.3524  0.0630  2.6836    1       0   
30     60.0    0       0         -1 -0.3703  0.0718  2.6836    1       0   
31     62.0    0       0         -1 -0.3883  0.0803  2.9899    1       0   
32     64.0    0       0         -1 -0.4083  0.0803 -3.1283    1       0   
33     66.0    0       0         -1 -0.4283  0.0800 -3.1283    1       0   
34     68.0    0       0         -1 -0.4457  0.0736 -2.0366    1       0   
35     70.0    0       0         -1 -0.4409  0.0565 -0.4658    1       0   
36     72.0    0       0         -1 -0.4213  0.0551  0.0133    1       0   
37     74.0    0       0         -1 -0.4013  0.0554  0.0133    1       0   
38     76.0    0       0         -1 -0.3813  0.0556  0.0133    1       0   
39     78.0    0       0         -1 -0.3613  0.0559  0.0133    1       1   
40     80.0    0       0         -1 -0.3413  0.0562  0.0133    1       1   
41     82.0    0       0         -1 -0.3213  0.0564  0.0133    1       1   
42     84.0    0       0         -1 -0.3013  0.0567  0.0133    1       1   
43     86.0    0       0         -1 -0.2813  0.0570  0.0133    1       1   
44     88.0    0       0         -1 -0.2613  0.0572  0.0133    1       1   
45     90.0    0       0         -1 -0.2414  0.0575  0.0133    1       1   
46     92.0    0       0         -1 -0.2214  0.0574 -0.0653    1       1   
47     94.0    0       0         -1 -0.2014  0.0561 -0.0653    1       1   
48     96.0    0       0         -1 -0.1815  0.0548 -0.0653    1       1   
49     98.0    0       0         -1 -0.1615  0.0535 -0.0653    1       1   
50    100.0    0       0         -1 -0.1416  0.0522 -0.0653    1       1   
51    102.0    0       0         -1 -0.1216  0.0509 -0.

In [26]:
total_exp_df.iloc[:2,:]

time_c  id0_c  state0_c area_type0_c  posx0_c  posy0_c  ori0_c  id1_c  \
0     0.1      0         0           -1  -0.2607   0.3622  0.4071      1   
1     2.0      0         0           -1  -0.2448   0.3572 -1.0773      1   

   state1_c area_type1_c  posx1_c  posy1_c  ori1_c  id2_c  state2_c  \
0         0           -1  -0.3433  -0.2326  1.0659      2         0   
1         0           -1  -0.3286  -0.2221  0.5161      2         0   

  area_type2_c  posx2_c  posy2_c  ori2_c  id3_c  state3_c area_type3_c  \
0           -1   0.2655   0.1613  2.6603      3         0           -1   
1           -1   0.2486   0.1686  2.7389      3         0           -1   

   posx3_c  posy3_c  ori3_c  id4_c  state4_c area_type4_c  posx4_c  posy4_c  \
0   0.3504  -0.1803 -0.7323      4         1           RR   0.0455   0.1321   
1   0.3525  -0.1967 -2.2167      4         1           RR   0.0455   0.1321   

   ori4_c  id5_c  state5_c area_type5_c  posx5_c  posy5_c  ori5_c  id6_c  \
0 -1.3097      5         0           BB   0.1563   0.2906  2.2984      6   
1 -1.3097      5         1           BB   0.1435   0.2979  2.6911      6   

   state6_c area_type6_c  posx6_c  posy6_c  ori6_c  id7_c  state7_c  \
0         0           -1  -0.1749   0.0956  1.6630      7         1   
1         0           -1  -0.1853   0.1100  2.3698      7         1   

  area_type7_c  posx7_c  posy7_c  ori7_c  id8_c  state8_c area_type8_c  \
0           RR   0.1683   0.1723 -0.6124      8         0           -1   
1           RR   0.1683   0.1723 -0.6124      8         0           -1   

   posx8_c  posy8_c  ori8_c  id9_c  state9_c area_type9_c  posx9_c  posy9_c  \
0  -0.3154  -0.0060  0.3881      9         0           -1   0.3558   0.2546   
1  -0.2978  -0.0086 -0.3187      9         0           -1   0.3444   0.2437   

   ori9_c  id10_c  state10_c area_type10_c  posx10_c  posy10_c  ori10_c  \
0 -1.6789      10          1            RB   -0.3088   -0.1252   1.7991   
1  3.1199      10          1            RB   -0.3088   -0.1252   1.7991   

   id11_c  state11_c area_type11_c  posx11_c  posy11_c  ori11_c  id12_c  \
0      11          1            RR    0.1779   -0.0835   1.7921      12   
1      11          1            RR    0.1779   -0.0835   1.7921      12   

   state12_c area_type12_c  posx12_c  posy12_c  ori12_c  id13_c  state13_c  \
0          0            -1    0.3197    0.2276  -1.3690      13          0   
1          0            BB    0.3293    0.2122  -0.9685      13          0   

  area_type13_c  posx13_c  posy13_c  ori13_c  id14_c  state14_c area_type14_c  \
0            -1    0.2292    0.1075  -0.6003      14          0            -1   
1            -1    0.2462    0.1006  -0.3647      14          0            -1   

   posx14_c  posy14_c  ori14_c  id15_c  state15_c area_type15_c  posx15_c  \
0   -0.2640   -0.2759   3.1336      15          0            -1   -0.3705   
1   -0.2766   -0.2866  -1.6651      15          0            -1   -0.3887   

   posy15_c  ori15_c  id16_c  state16_c area_type16_c  posx16_c  posy16_c  \
0    0.0185   2.7454      16          0            -1    0.2800   -0.2027   
1    0.0186  -3.0665      16          0            -1    0.2707   -0.2164   

   ori16_c  id17_c  state17_c area_type17_c  posx17_c  posy17_c  ori17_c  \
0  -2.8764      17          0            -1   -0.1025    0.0139   1.3230   
1  -1.3920      17          0            -1   -0.0910    0.0278   0.7733   

   id18_c  state18_c area_type18_c  posx18_c  posy18_c  ori18_c  id19_c  \
0      18          0            -1   -0.2547    0.0614   1.2143      19   
1      18          0            -1   -0.2584    0.0786   1.9997      19   

   state19_c area_type19_c  posx19_c  posy19_c  ori19_c  id20_c  state20_c  \
0          0            -1    0.2447    0.0239   1.5360      20          1   
1          0            -1    0.2560    0.0361   0.0516      20          1   

  area_type20_c  posx20_c  posy20_c  ori20_c  id21_c  state21_c area_type21_c  \
0            BR   -0.0931   -

In [29]:
dfPath = "/home/luigi/Documents/ARGoS/argos_results_scripts/DHTF/results_brownian/four_regions/four_regions_2021-05-03_robots#24_timeout#180_redAreas#4_1800seconds/kiloLOG_timeout#1800_.pickle"

In [30]:
timeout_180_df = pd.read_pickle(dfPath)